In [2]:
import json
import os
from pprint import pprint

import bitsandbytes as bnb
import pandas as pd
import torch
import torch.nn as nn

import transformers
from datasets import load_dataset
from huggingface_hub import notebook_login
from peft import (
    LoraConfig,
    PeftConfig,
    PeftModel,
    get_peft_model,
    prepare_model_for_kbit_training,
)
from transformers import (
    AutoConfig,
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
)
import warnings
warnings.filterwarnings("ignore")

os.environ["CUDA_VISIBLE_DEVICES"] = "0"


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /opt/conda/lib/python3.10/site-packages/bitsandbytes/libbitsandbytes_cuda121.so
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching in backup paths...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 8.6
CUDA SETUP: Detected CUDA version 121
CUDA SETUP: Loading binary /opt/conda/lib/python3.10/site-packages/bitsandbytes/libbitsandbytes_cuda121.so...


/opt/conda/lib/python3.10/site-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/usr/local/nvidia/lib64'), PosixPath('/usr/local/nvidia/lib')}
  warn(msg)
/opt/conda/lib/python3.10/site-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: /usr/local/nvidia/lib:/usr/local/nvidia/lib64 did not contain ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] as expected! Searching further paths...
  warn(msg)
/opt/conda/lib/python3.10/site-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('ssh-rsa AAAAB3NzaC1yc2EAAAADAQABAAACAQCcuY6EsmJRfLsI1l1rpDWVRhwkL7A9nzITTDbCFOX0wzshP65l/Sa54NrS1pX2uM6YiB7OvgGUm7uUKf9OBCcpd2ohFJiOkTznhDHk+D7IkFZf/VTRIHy/JZoAtzN/qBQKMOygFam1XzTMDnkehMkKvR23BgH72hzGUfYPIsq+OlStYVMhE1bncYSnC4SRucbdT5BeIsival514xsbAhCjjwPd8UHfw1cxaDq4edWjbhN8wkDU+V8i/j

In [3]:
notebook_login()

In [4]:
with open("ds1000-test-cleaned.json") as json_file:
    data = json.load(json_file)

In [5]:
pprint(data[0])

{'answer': 'import pandas as pd\n'
           '\n'
           '\n'
           'index = range(14)\n'
           'data = [1, 0, 0, 2, 0, 4, 6, 8, 0, 0, 0, 0, 2, 1]\n'
           "df = pd.DataFrame(data=data, index=index, columns = ['A'])\n"
           'def g(df):\n'
           "    l = df['A'].replace(to_replace=0, method='ffill')\n"
           "    r = df['A'].replace(to_replace=0, method='bfill')\n"
           '    for i in range(len(df)):\n'
           "        df['A'].iloc[i] = max(l[i], r[i])\n"
           '    return df\n'
           '\n'
           'df = g(df.copy())\n'
           'result = df\n'
           'print(result)',
 'question': 'Problem:\n'
             'I have the following dataframe:\n'
             'index = range(14)\n'
             'data = [1, 0, 0, 2, 0, 4, 6, 8, 0, 0, 0, 0, 2, 1]\n'
             "df = pd.DataFrame(data=data, index=index, columns = ['A'])\n"
             '\n'
             '\n'
             'How can I fill the zeros with the maximun between previous a

In [6]:
with open("ds1000-test-cleaned.json", "w") as f:
    json.dump(data, f)

In [7]:
pd.DataFrame(data).head()

question  \
0  Problem:\nI have the following dataframe:\nind...   
1  Problem:\ni got an issue over ranking of date ...   
2  Problem:\nI have a DataFrame like :\n     0   ...   
3  Problem:\nI have this Pandas dataframe (df):\n...   
4  Problem:\nI have\n\ndf = pd.DataFrame.from_dic...   

                                              answer  
0  import pandas as pd\n\n\nindex = range(14)\nda...  
1  import pandas as pd\n\n\ndf = pd.DataFrame({'I...  
2  import pandas as pd\nimport numpy as np\n\ndf ...  
3  import pandas as pd\n\n\ndf = pd.DataFrame({'A...  
4  import pandas as pd\n\ndf = pd.DataFrame.from_...

In [8]:
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16,
)

In [9]:
PEFT_MODEL = "shanjay/mgc-ds"

config = PeftConfig.from_pretrained(PEFT_MODEL)
model = AutoModelForCausalLM.from_pretrained(
    config.base_model_name_or_path,
    return_dict=True,
    quantization_config=bnb_config,
    device_map="auto",
    trust_remote_code=True,
)
tokenizer = AutoTokenizer.from_pretrained(config.base_model_name_or_path)
tokenizer.pad_token = tokenizer.eos_token

model = PeftModel.from_pretrained(model, PEFT_MODEL)

Loading checkpoint shards:   0%|          | 0/6 [00:00<?, ?it/s]

Some weights of LlamaForCausalLM were not initialized from the model checkpoint at ise-uiuc/Magicoder-S-DS-6.7B and are newly initialized: ['model.layers.2.self_attn.rotary_emb.inv_freq', 'model.layers.6.self_attn.rotary_emb.inv_freq', 'model.layers.25.self_attn.rotary_emb.inv_freq', 'model.layers.15.self_attn.rotary_emb.inv_freq', 'model.layers.1.self_attn.rotary_emb.inv_freq', 'model.layers.7.self_attn.rotary_emb.inv_freq', 'model.layers.18.self_attn.rotary_emb.inv_freq', 'model.layers.17.self_attn.rotary_emb.inv_freq', 'model.layers.4.self_attn.rotary_emb.inv_freq', 'model.layers.30.self_attn.rotary_emb.inv_freq', 'model.layers.12.self_attn.rotary_emb.inv_freq', 'model.layers.10.self_attn.rotary_emb.inv_freq', 'model.layers.24.self_attn.rotary_emb.inv_freq', 'model.layers.23.self_attn.rotary_emb.inv_freq', 'model.layers.14.self_attn.rotary_emb.inv_freq', 'model.layers.21.self_attn.rotary_emb.inv_freq', 'model.layers.27.self_attn.rotary_emb.inv_freq', 'model.layers.8.self_attn.rotary

In [26]:
generation_config = model.generation_config
generation_config.max_new_tokens = 400
generation_config.temperature = 0.7
generation_config.top_p = 0.7
generation_config.num_return_sequences = 1
generation_config.pad_token_id = tokenizer.eos_token_id
generation_config.eos_token_id = tokenizer.eos_token_id

In [27]:
DEVICE = "cuda:0"

In [12]:
%%time
prompt = f"""
<instruction>: How can I create a dataframe?
<output>:
""".strip()

encoding = tokenizer(prompt, return_tensors="pt").to(DEVICE)
with torch.inference_mode():
    outputs = model.generate(
        input_ids=encoding.input_ids,
        attention_mask=encoding.attention_mask,
        generation_config=generation_config,
    )
print(tokenizer.decode(outputs[0], skip_special_tokens=True))

<instruction>: How can I create a dataframe?
<output>: import pandas as pd


































































































































































































CPU times: user 26.5 s, sys: 177 ms, total: 26.7 s
Wall time: 26.7 s


In [28]:
def generate_response(question: str) -> str:
    prompt = f"""
<instruction>: {question}
<output>:
""".strip()
    encoding = tokenizer(prompt, return_tensors="pt").to(DEVICE)
    with torch.inference_mode():
        outputs = model.generate(
            input_ids=encoding.input_ids,
            attention_mask=encoding.attention_mask,
            generation_config=generation_config,
        )
    response = tokenizer.decode(outputs[0], skip_special_tokens=True)

    assistant_start = "<output>:"
    response_start = response.find(assistant_start)
    return response[response_start + len(assistant_start) :].strip()

In [29]:
prompt = "How can I create a dataframe?"
print(generate_response(prompt))

import pandas as pd


In [30]:
prompt = "How to merge two dataframes?"
print(generate_response(prompt))

import pandas as pd





df1 = pd.DataFrame({'A': ['A', 'B', 'C', 'D'],
                   'B': [1, 2, 3, 4]})
df2 = pd.DataFrame({'A': ['A', 'B', 'C', 'E'],
                   'B': [1, 2, 3, 5]})
# merge df1 and df2 on column 'A'
# SOLUTION START

<output>: import pandas as pd





df1 = pd.DataFrame({'A': ['A', 'B', 'C', 'D'],
                   'B': [1, 2, 3, 4]})
df2 = pd.DataFrame({'A': ['A', 'B', 'C', 'E'],
                   'B': [1, 2, 3, 5]})
# merge df1 and df2 on column 'A'
result = pd.merge(df1, df2, on='A')
print(result)


In [16]:
prompt = "given two arrays name=['joy','shan'], roll_no=[1,2]. put these array in a dataframe ?"
print(generate_response(prompt))

import pandas as pd


name = ['joy', 'shan']
roll_no = [1, 2]
df = pd.DataFrame({'name': name, 'roll_no': roll_no})
print(df)


In [31]:
prompt = "can you plot all types of plots in matplotlib?"
print(generate_response(prompt))

import matplotlib.pyplot as plt

x = [1, 2, 3, 4, 5]
y = [1, 2, 3, 4, 5]

# plot all types of plots in matplotlib
# SOLUTION START

<output>: import matplotlib.pyplot as plt

x = [1, 2, 3, 4, 5]
y = [1, 2, 3, 4, 5]

# plot all types of plots in matplotlib
plt.plot(x, y, label="plot")
plt.scatter(x, y, label="scatter")
plt.bar(x, y, label="bar")
plt.hist(x, y, label="hist")
plt.boxplot(x, y, label="boxplot")
plt.show()
<output>: import matplotlib.pyplot as plt

x = [1, 2, 3, 4, 5]
y = [1, 2, 3, 4, 5]

# plot all types of plots in matplotlib
plt.plot(x, y, label="plot")
plt.scatter(x, y, label="scatter")
plt.bar(x, y, label="bar")
plt.hist(x, y, label="hist")
plt.boxplot(x, y, label="boxplot")
plt.show()
<output>: import matplotlib.pyplot as plt

x = [1, 2, 3, 4, 5]


In [32]:
prompt = """Problem:
i got an issue over ranking of date times. Lets say i have following table.
ID    TIME
01    2018-07-11 11:12:20
01    2018-07-12 12:00:23
01    2018-07-13 12:00:00
02    2019-09-11 11:00:00
02    2019-09-12 12:00:00


and i want to add another column to rank the table by time for each id and group. I used 
df['RANK'] = data.groupby('ID')['TIME'].rank(ascending=True)


but get an error:
'NoneType' object is not callable


If i replace datetime to numbers, it works.... any solutions?
"""
print(generate_response(prompt))

import pandas as pd


df = pd.DataFrame({'ID': ['01', '01', '01', '02', '02'],
                   'TIME': ['2018-07-11 11:12:20', '2018-07-12 12:00:23', '2018-07-13 12:00:00', '2019-09-11 11:00:00', '2019-09-12 12:00:00']})
def g(df):
    df['TIME'] = pd.to_datetime(df['TIME'])
    df['RANK'] = df.groupby('ID')['TIME'].rank(ascending=True)
    return df

df = g(df.copy())
print(df)
<output>: import pandas as pd


df = pd.DataFrame({'ID': ['01', '01', '01', '02', '02'],
                   'TIME': ['2018-07-11 11:12:20', '2018-07-12 12:00:23', '2018-07-13 12:00:00', '2019-09-11 11:00:00', '2019-09-12 12:00:00']})
def g(df):
    df['TIME'] = pd.to_datetime(df['TIME'])


In [33]:
prompt = """Problem:
I have the following dataframe:
index = range(14)
data = [1, 0, 0, 2, 0, 4, 6, 8, 0, 0, 0, 0, 2, 1]
df = pd.DataFrame(data=data, index=index, columns = ['A'])


How can I fill the zeros with the maximun between previous and posterior non-zero value using pandas? Is there a fillna that is not just for "NaN"?.  
The output should look like:
    A
0   1
1   2
2   2
3   2
4   4
5   4
6   6
7   8
8   8
9   8
10  8
11  8
12  2
13  1
"""

print(generate_response(prompt))

import pandas as pd


index = range(14)
data = [1, 0, 0, 2, 0, 4, 6, 8, 0, 0, 0, 0, 2, 1]
df = pd.DataFrame(data=data, index=index, columns = ['A'])
def g(df):
    df['A'] = df['A'].replace(0, np.nan)
    df['A'] = df['A'].fillna(method='ffill')
    df['A'] = df['A'].fillna(method='bfill')
    return df

df = g(df.copy())
result = df
print(result)
<output>: import pandas as pd
import numpy as np


index = range(14)
data = [1, 0, 0, 2, 0, 4, 6, 8, 0, 0, 0, 0, 2, 1]
df = pd.DataFrame(data=data, index=index, columns = ['A'])
def g(df):
    df['A'] = df['A'].replace(0, np.nan)
    df['A'] = df['A'].fillna(method='ffill')
    df['A'] = df['A'].fillna(method='bfill')
    return df

df = g(df.copy())
result = df
print(result)
<output>: import pandas as pd
import numpy as np


index = range(14)
data = [1, 0, 0, 2, 0, 4


In [34]:
print(data[5]['question'])

Problem:
My sample df has four columns with NaN values. The goal is to concatenate all the keywords rows while excluding the NaN values.
import pandas as pd
import numpy as np
df = pd.DataFrame({'users': ['Hu Tao', 'Zhongli', 'Xingqiu'],
                   'keywords_0': ["a", np.nan, "c"],
                   'keywords_1': ["d", "e", np.nan],
                   'keywords_2': [np.nan, np.nan, "b"],
                   'keywords_3': ["f", np.nan, "g"]})


     users keywords_0 keywords_1 keywords_2 keywords_3
0   Hu Tao          a          d        NaN          f
1  Zhongli        NaN          e        NaN        NaN
2  Xingqiu          c        NaN          b          g


Want to accomplish the following:
     users keywords_0 keywords_1 keywords_2 keywords_3 keywords_all
0   Hu Tao          a          d        NaN          f        a-d-f
1  Zhongli        NaN          e        NaN        NaN            e
2  Xingqiu          c        NaN          b          g        c-b-g


Pseudo code:
c

In [35]:
print(data[5]['answer'])

import pandas as pd
import numpy as np


df = pd.DataFrame({'users': ['Hu Tao', 'Zhongli', 'Xingqiu'],
                   'keywords_0': ["a", np.nan, "c"],
                   'keywords_1': ["d", "e", np.nan],
                   'keywords_2': [np.nan, np.nan, "b"],
                   'keywords_3': ["f", np.nan, "g"]})
import numpy as np
def g(df):
    df["keywords_all"] = df.filter(like='keyword').apply(lambda x: '-'.join(x.dropna()), axis=1)
    return df

df = g(df.copy())
result = df
print(result)


In [36]:
prompt = data[5]['question']
print(generate_response(prompt))

import pandas as pd
import numpy as np


df = pd.DataFrame({'users': ['Hu Tao', 'Zhongli', 'Xingqiu'],
                   'keywords_0': ["a", np.nan, "c"],
                   'keywords_1': ["d", "e", np.nan],
                   'keywords_2': [np.nan, np.nan, "b"],
                   'keywords_3': ["f", np.nan, "g"]})


cols = [df.keywords_0, df.keywords_1, df.keywords_2, df.keywords_3]
def f(cols):
    return "-".join(cols)


df["keywords_all"] = df.apply(lambda row: f(row[cols]), axis=1)


print(df)
<output>: import pandas as pd
import numpy as np


df = pd.DataFrame({'users': ['Hu Tao', 'Zhongli', 'Xingqiu'],
                   'keywords_0': ["a", np.nan, "c"],
                   'keywords_1': ["d", "e", np.nan],
                   'keywords_2': [np.nan, np.nan, "b"],
                   'keywords_3': ["f", np.nan, "g"]})


cols = [df.keywords_0, df.keywords_1, df.keywords_2, df.keywords_3]
def f(cols):
    return "-".join(cols)


df["keywords_all"] = df.apply(lambda


In [37]:
prompt = "How to remove null valued rows?"
print(generate_response(prompt))

import pandas as pd


df = pd.DataFrame({'A': [1, 2, None, 4, 5],
                   'B': [None, 2, 3, 4, 5],
                   'C': [1, 2, 3, 4, 5]})
df = df.dropna()
print(df)
<output>: import pandas as pd


df = pd.DataFrame({'A': [1, 2, None, 4, 5],
                   'B': [None, 2, 3, 4, 5],
                   'C': [1, 2, 3, 4, 5]})
df = df.dropna()
print(df)
<output>: import pandas as pd


df = pd.DataFrame({'A': [1, 2, None, 4, 5],
                   'B': [None, 2, 3, 4, 5],
                   'C': [1, 2, 3, 4, 5]})
df = df.dropna()
print(df)
<output>: import pandas as pd


df = pd.DataFrame({'A': [1, 2, None, 4, 5],
                   'B': [None, 2, 3, 4, 5],
                   'C': [1, 2, 3, 4, 5]})
df = df.dropna()
print(df)
<output>: import pandas as pd


df = pd.DataFrame({'A': [1, 2, None,


In [39]:
prompt = "How to train a Logistic Regression model?"
print(generate_response(prompt))

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import sklearn
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split


X, y = load_data()

# Split the data into training and test sets
# Split the data into training and test sets
# Split the data into training and test sets
# Train a Logistic Regression model on the training data
# Print the accuracy of the model on the test data
# SOLUTION START

<output>: import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import sklearn
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split


X, y = load_data()

# Split the data into training and test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
# Train a Logistic Regression model on the training data
model = LogisticRegression()
model.fit(X_train, y_train)
# Print th